In [7]:
import pandas as pd
import numpy as np
import glob
from pathlib import Path
from tqdm import tqdm
import significantdigits as sd

force = False

# Run this script from the notebooks directory
root_dir = Path().resolve()
input_path = Path().resolve() / "results" / "abide"
output_path = Path().resolve().parent / "results" / "stats"
#output_path.mkdir(parents=True, exist_ok=True)
print(f"Input path: {input_path}")
print(f"Output path: {output_path}")

Input path: /home/yohan/Work/mriqc-fuzzy/notebooks/results/abide
Output path: /home/yohan/Work/mriqc-fuzzy/results/stats


In [8]:
def parse_file(filename):
    df_data = pd.read_json(filename)
    meta = df_data['bids_meta']
    result = pd.DataFrame([df_data.drop(columns=['bids_meta']).iloc[0]])
    result['subject'] = meta['subject']
    return result

from concurrent.futures import ProcessPoolExecutor, as_completed
from pathlib import Path
from typing import Optional
import pandas as pd
from tqdm import tqdm

# Assumes parse_file(path: Path) -> pd.DataFrame already exists

def _parse_one(path: Path) -> Optional[pd.DataFrame]:
    """Worker-safe wrapper around parse_file that adds metadata."""
    try:
        df = parse_file(path)
        # Be defensive about how we extract 'repetition'
        # Your original used parts[-5]; keep that, but fall back gracefully.
        try:
            repetition = int(Path(path).parts[-5])
        except Exception:
            # Try to infer from common BIDS-like patterns; otherwise mark as NaN
            repetition = pd.NA
        df['repetition'] = repetition
        df['file'] = path.as_posix()
        return df
    except Exception as e:
        # Return a tiny DataFrame with the error to avoid losing diagnostics
        # (you can also return None to skip on error)
        return pd.DataFrame({
            "file": [path.as_posix()],
            "error": [repr(e)]
        })

def parse_files(directory: Path, force: bool = False, n_workers: int = 8) -> pd.DataFrame:
    """
    Parallel recursive parse of anat/*.json files under `directory`.

    Parameters
    ----------
    directory : Path
        Root directory to search.
    force : bool
        If False and CSV exists, load and return it. If True, re-parse everything.
    n_workers : int
        Number of worker processes for parallel parsing.

    Returns
    -------
    pd.DataFrame
        Concatenated results with 'repetition' and 'file' columns.
    """
    out_csv = output_path / "abide_metrics.csv"
    if not force and out_csv.exists():
        print("File already exists, skipping parsing.")
        return pd.read_csv(out_csv)

    json_paths = list(directory.rglob('anat/*.json'))
    if not json_paths:
        # Nothing to do; return empty DataFrame with expected columns
        return pd.DataFrame(columns=["repetition", "file"])

    results = []
    # Use a temp file for atomic write
    out_tmp = out_csv.with_suffix(".csv.tmp")

    # Chunked submission to avoid overwhelming the executor with huge job lists
    # (still fine to submit all at once for most cases)
    with ProcessPoolExecutor(max_workers=max(1, n_workers)) as ex:
        futures = {ex.submit(_parse_one, p): p for p in json_paths}
        for fut in tqdm(as_completed(futures), total=len(futures), desc="Parsing JSONs", unit="file"):
            df = fut.result()
            # Skip totally empty returns (shouldn't happen here)
            if df is None:
                continue
            results.append(df)

    # Concatenate; handle the case where some workers returned error rows
    df = pd.concat(results, ignore_index=True) if results else pd.DataFrame()

    # If you included error rows above, you can separate them like this:
    # err_rows = df.columns.__contains__("error")
    # if err_rows:
    #     print(f"Encountered {df['error'].notna().sum()} parse errors.")

    # Persist atomically
    out_tmp.parent.mkdir(parents=True, exist_ok=True)
    df.to_csv(out_tmp, index=False)
    out_tmp.replace(out_csv)

    return df

df_files = parse_files(input_path, force=force)

File already exists, skipping parsing.


In [9]:
def get_fields(json_file):
  fields = Path(json_file).parts
  return {'PATNO': fields[-4], 
          'repetition': int(fields[-5]),
          'modality': fields[-6],
          'site': fields[-7],
          'dataset': fields[-9],
          'file': str(json_file)
          }

df_files['file'] = df_files['file'].astype(str)
df_fields = df_files['file'].apply(get_fields).apply(pd.Series)
df = pd.merge(df_files, df_fields, left_on=['file', 'repetition'], right_on=['file', 'repetition'])

In [10]:
id_vars = ['subject', 'repetition', 'file', 'PATNO', 'modality', 'site', 'dataset']
df.drop(columns=['provenance'], inplace=True, errors='ignore')
df_raw = pd.melt(df, id_vars=id_vars, 
        value_vars=[col for col in df.columns if col not in id_vars])
df_raw['subject'] = df_raw['subject'].astype(int)
df_raw.to_csv(output_path / "abide_metrics_raw.csv", index=False)

In [11]:
# Higher values means better quality
positive_correlation = ['cnr', 'snr', 'snrd', 'fber', 'inu_med', 'inu_range', 'tpm_overlap_csf',
                        'tpm_overlap_gm', 'tpm_overlap_wm']
# Lower values means better quality
negative_correlation = ['cjv', 'qi_2', 'efc', 'qi_1', 'fwhm_avg', 'fwhm_x', 'fwhm_y', 'fwhm_z', 'qi_1', 'qi_2',
                        'rpve_csf', 'rpve_gm', 'rpve_wm', 'wm2max']

# Intracranial volume fractions
# Estimation of the icv of each tissue calculated on the FSL FAST’s segmentation. Normative values fall around 20%, 45% and 35% for cerebrospinal fluid (CSF), WM and GM, respectively.
icvs = ['icvs_csf', 'icvs_gm', 'icvs_wm']


## Distribution numerical variability across subjects

In [12]:
print(f"Force is set to {force}")
print(f"Output path exists: {output_path.exists()}")
if True or force or not (output_path / "abide_metrics_stats.csv").exists():
  id_vars = ['subject', 'PATNO', 'repetition', 'modality', 'site', 'dataset', 'file']  
  stats= df.melt(id_vars=id_vars).groupby(['subject','PATNO','variable','site'])['value'].agg(['mean', 'std', 'var', 'min', 'max', lambda x : float(sd.significant_digits(x, reference=np.mean(x), basis=10))]).clip(lower=0)
  stats.columns = ['mean', 'std', 'var', 'min', 'max', 'sig_digits']
  stats = stats.reset_index()
  print(f"Saving stats to {output_path / 'abide_metrics_stats.csv'}")
  stats.to_csv(output_path / "abide_metrics_stats.csv", index=False)

stats  = pd.read_csv(output_path / "abide_metrics_stats.csv")

Force is set to False
Output path exists: True


/home/yohan/.local/lib/python3.10/site-packages/significantdigits/_significantdigits.py:452: UserWarning: error is set to relative and the reference has 0 leading to NaN
  warnings.warn(warn_msg)
/home/yohan/.local/lib/python3.10/site-packages/significantdigits/_significantdigits.py:283: RuntimeWarning: invalid value encountered in divide
  return operator(x, y_expanded)


Saving stats to /home/yohan/Work/mriqc-fuzzy/results/stats/abide_metrics_stats.csv


In [15]:
good = pd.read_csv(root_dir / "abide_annotations" / "good_quality_scans.csv")
bad = pd.read_csv(root_dir / "abide_annotations" / "scans_with_artifacts.csv")

qc_annotations = pd.concat([good.assign(qc='good'), bad.assign(qc='bad')])
qc_annotations['site'] = qc_annotations['0'].str.split('-').apply(lambda x: x[:-1]).str.join('-')
qc_annotations['PATNO'] = qc_annotations['0'].str.split('-').apply(lambda x: x[-1]).astype(int)
qc_annotations.drop(columns=['0'], inplace=True)

In [16]:
qc_ = qc_annotations.melt(id_vars=['site', 'PATNO', 'qc'], value_vars=['Image sharpness', 'Ringing', 'CNR subcortical structures', 'CNR GM and WM'], var_name='qc_metric', value_name='qc_value')
df_raw_qc = pd.merge(df_raw, qc_, left_on=['site', 'subject'], right_on=['site', 'PATNO']).drop(columns=['file', 'modality', 'PATNO_x', 'PATNO_y', 'qc'])
df_raw_qc = df_raw_qc[df_raw_qc['variable'] != 'provenance']
df_raw_qc.to_csv(output_path / "abide_metrics_raw_qc.csv", index=False)

In [17]:
stats_qc = pd.merge(stats.drop(columns=['PATNO']), qc_annotations, left_on=['site', 'subject'], right_on=['site', 'PATNO'])
id_vars = ['subject', 'variable', 'site', 'mean', 'std', 'var', 'min', 'max', 'sig_digits', 'qc', 'PATNO']
values = ['Image sharpness', 'Ringing', 'CNR subcortical structures', 'CNR GM and WM']
stats_qc_m = pd.melt(stats_qc, id_vars=id_vars, value_vars=values, var_name='QC_metric', value_name='QC_value')
stats_qc.to_csv(output_path / "abide_metrics_stats_qc.csv", index=False)

In [18]:
import plotly.express as px
import plotly

(px.scatter(stats, x='mean', y='std', color='site', opacity=1, log_x=True, log_y=True, title='Mean vs Standard Deviation across subjects per metric', hover_name='variable',height=800, color_discrete_sequence=plotly.colors.qualitative.T10)
 .update_xaxes(exponentformat='power')
 .update_yaxes(exponentformat='power')
 .add_scatter(x=np.logspace(-5,7,10), y=np.logspace(-5,7,10), mode='lines', line=dict(color='black', dash='dash'), name='0 sig', showlegend=True)
 .add_scatter(x=np.logspace(-5,7,10), y=np.logspace(-5,7,10)*10**-2, mode='lines', line=dict(color='DarkGray', dash='dash'), name='2 sig', showlegend=True)
 .add_scatter(x=np.logspace(-5,7,10), y=np.logspace(-5,7,10)*10**-4, mode='lines', line=dict(color='LightGray', dash='dash'), name='4 sig', showlegend=True)
 .add_scatter(x=np.logspace(-5,7,10), y=np.logspace(-5,7,10)*10**-6, mode='lines', line=dict(color='white', dash='dash'), name='6 sig', showlegend=True)
)

In [19]:
import plotly.express as px
import plotly.graph_objects as go
import plotly

stats_summary = stats[stats.variable.str.contains('summary')]
stats_summary_comp = stats[~stats.variable.str.contains('summary')]
stats_summary.sort_values(by=['sig_digits'], ascending=[False], inplace=True)
stats_summary['category'] = stats_summary['variable'].apply(lambda x: x.split('_')[-1])
stats_summary['tissue'] = stats_summary['variable'].apply(lambda x: x.split('_')[1])
fig = go.Figure()
fig = px.strip(stats_summary, x='sig_digits', y='variable', color='site', facet_row='category', facet_col='tissue', title='Significant digits distribution across subject per metric', height=1600, color_discrete_sequence=plotly.colors.qualitative.T10)
fig.update_xaxes(range=[0, 5])
fig.update_yaxes(matches=None)
display(fig)
for group in [positive_correlation, negative_correlation, icvs]:
    stats_summary_comp_group = stats_summary_comp[stats_summary_comp.variable.isin(group)]
    stats_summary_comp_group.sort_values(by=['sig_digits'], ascending=[False], inplace=True)
    fig = px.strip(stats_summary_comp_group, y='sig_digits', x='variable', color='site', title='Significant digits distribution across subject per metric', color_discrete_sequence=plotly.colors.qualitative.T10)
    display(fig)

/tmp/ipykernel_4621/4145637614.py:7: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/tmp/ipykernel_4621/4145637614.py:8: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/tmp/ipykernel_4621/4145637614.py:9: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



/tmp/ipykernel_4621/4145637614.py:17: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



/tmp/ipykernel_4621/4145637614.py:17: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



/tmp/ipykernel_4621/4145637614.py:17: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [20]:
stats_summary_annotated = pd.merge(stats_summary, qc_annotations, left_on=['subject', 'site'], right_on=['PATNO', 'site'])
stats_summary_comp_annotated = pd.merge(stats_summary_comp, qc_annotations, left_on=['subject', 'site'], right_on=['PATNO', 'site'])

## Spearman correlation

In [21]:
import sys
import scipy as sp
from scipy.stats import spearmanr, kendalltau

def get_correlation(df, verbose=False):
    qc_metrics = ['Image sharpness', 'Ringing', 'CNR subcortical structures', 'CNR GM and WM']
    correlation = pd.DataFrame(columns=['variable', 'metric', 'correlation', 'p_value', 'method', 'qc_metric'])
    fo = open('/dev/null', 'w') if not verbose else sys.stdout

    sg = df.groupby('variable')
    for qc_metric in qc_metrics:
        print(f"QC Metric: {qc_metric}", file=fo)
        for name, group in sg:
            print(f"Variable: {name}", file=fo)
            group = group.dropna(subset=['mean', 'std', qc_metric])        
            rho_mean, p_mean = sp.stats.spearmanr(group[qc_metric], group['mean'])
            rho_std, p_std = sp.stats.spearmanr(group[qc_metric], np.log(group['std']))
            rho_sig, p_sig = sp.stats.spearmanr(group[qc_metric], group['sig_digits'])
            print(f"Spearman correlation between {qc_metric} and mean: rho={rho_mean:.3f}, p={p_mean:.3e}", file=fo)
            print(f"Spearman correlation between {qc_metric} and std: rho={rho_std:.3f}, p={p_std:.3e}", file=fo)
            print(f"Spearman correlation between {qc_metric} and sig_digits: rho={rho_sig:.3f}, p={p_sig:.3e}", file=fo)
            correlation = pd.concat([correlation, pd.DataFrame({'variable': name, 'metric': 'mean', 'correlation': rho_mean, 'p_value': p_mean, 'method': 'spearman', 'qc_metric': qc_metric}, index=[0])], ignore_index=True)
            correlation = pd.concat([correlation, pd.DataFrame({'variable': name, 'metric': 'std', 'correlation': rho_std, 'p_value': p_std, 'method': 'spearman', 'qc_metric': qc_metric}, index=[0])], ignore_index=True)
            correlation = pd.concat([correlation, pd.DataFrame({'variable': name, 'metric': 'sig_digits', 'correlation': rho_sig, 'p_value': p_sig, 'method': 'spearman', 'qc_metric': qc_metric}, index=[0])], ignore_index=True)

            rho_mean, p_mean = sp.stats.kendalltau(group[qc_metric], group['mean'])
            rho_std, p_std = sp.stats.kendalltau(group[qc_metric], np.log(group['std']))
            rho_sig, p_sig = sp.stats.kendalltau(group[qc_metric], group['sig_digits'])
            print(f"Kendall correlation between {qc_metric} and mean: rho={rho_mean:.3f}, p={p_mean:.3e}", file=fo)
            print(f"Kendall correlation between {qc_metric} and std: rho={rho_std:.3f}, p={p_std:.3e}", file=fo)
            print(f"Kendall correlation between {qc_metric} and sig_digits: rho={rho_sig:.3f}, p={p_sig:.3e}", file=fo)
            correlation = pd.concat([correlation, pd.DataFrame({'variable': name, 'metric': 'mean', 'correlation': rho_mean, 'p_value': p_mean, 'method': 'kendall', 'qc_metric': qc_metric}, index=[0])], ignore_index=True)
            correlation = pd.concat([correlation, pd.DataFrame({'variable': name, 'metric': 'std', 'correlation': rho_std, 'p_value': p_std, 'method': 'kendall', 'qc_metric': qc_metric}, index=[0])], ignore_index=True)
            correlation = pd.concat([correlation, pd.DataFrame({'variable': name, 'metric': 'sig_digits', 'correlation': rho_sig, 'p_value': p_sig, 'method': 'kendall', 'qc_metric': qc_metric}, index=[0])], ignore_index=True)
    return correlation

In [22]:
correlation = get_correlation(stats_summary_annotated)
correlation_spearman = correlation[correlation.method == 'spearman']
correlation_spearman = correlation_spearman.copy()
correlation_spearman['significant'] = correlation_spearman['p_value'] < 0.05
correlation_spearman['category'] = correlation_spearman['variable'].apply(lambda x: x.split('_')[-1])
correlation_spearman['tissue'] = correlation_spearman['variable'].apply(lambda x: x.split('_')[1])
display(correlation_spearman)
fig = px.scatter(
	correlation_spearman.sort_values(by=['metric', 'correlation'], ascending=False),
	x='correlation',
	y='metric',
	color='qc_metric',
	symbol='significant',
	facet_row='category',
	facet_col='tissue',
	title='Correlation between QC Metrics and Variables (Spearman)',
	height=1800,
 	width=1200,
)
fig.update_yaxes(matches=None)
display(fig)



/tmp/ipykernel_4621/2570646539.py:22: FutureWarning:

The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.

/home/yohan/.local/lib/python3.10/site-packages/pandas/core/arraylike.py:399: RuntimeWarning:

divide by zero encountered in log

/tmp/ipykernel_4621/2570646539.py:17: ConstantInputWarning:

An input array is constant; the correlation coefficient is not defined.

/tmp/ipykernel_4621/2570646539.py:16: ConstantInputWarning:

An input array is constant; the correlation coefficient is not defined.



variable      metric  correlation       p_value    method  \
0       summary_bg_k        mean    -0.171483  2.221022e-03  spearman   
1       summary_bg_k         std    -0.157511  5.009561e-03  spearman   
2       summary_bg_k  sig_digits    -0.022376  6.919261e-01  spearman   
6     summary_bg_mad        mean     0.093856  9.528688e-02  spearman   
7     summary_bg_mad         std          NaN           NaN  spearman   
..               ...         ...          ...           ...       ...   
757   summary_wm_p95         std     0.113916  4.268253e-02  spearman   
758   summary_wm_p95  sig_digits    -0.129776  2.081904e-02  spearman   
762  summary_wm_stdv        mean     0.353395  9.333964e-11  spearman   
763  summary_wm_stdv         std     0.054580  3.327156e-01  spearman   
764  summary_wm_stdv  sig_digits     0.075005  1.828500e-01  spearman   

           qc_metric  significant category tissue  
0    Image sharpness         True        k     bg  
1    Image sharpness         True        k     bg  
2    Image sharpness        False        k     bg  
6    Image sharpness        False      mad     bg  
7    Image sharpness        False      mad     bg  
..               ...          ...      ...    ...  
757    CNR GM and WM         True      p95     wm  
758    CNR GM and WM         True      p95     wm  
762    CNR GM and WM         True     stdv     wm  
763    CNR GM and WM        False     stdv     wm  
764    CNR GM and WM        False     stdv     wm  

[384 rows x 9 columns]

In [24]:
from rich.console import Console
from rich.table import Table
from rich import box

# Render correlation_spearman using rich in the notebook/terminal

for metric in correlation_spearman['metric'].unique():
  for qc_metric in correlation_spearman['qc_metric'].unique():
    print(f"Metric: {metric}, QC Metric: {qc_metric}")
    console = Console()

    # Ensure variable exists
    if 'correlation_spearman' not in globals():
      raise NameError("correlation_spearman is not defined. Run the cell that creates it (e.g. cell 13 or 15).")

    df = correlation_spearman.copy()

    # Columns to show (keep only those present)
    cols = ['variable',  'qc_metric', 'correlation', 'p_value', 'significant', 'category', 'tissue']
    cols = [c for c in cols if c in df.columns]

    # Show top N rows by absolute correlation to keep output manageable
    top_n = 300
    df = df.reindex(df.correlation.abs().sort_values(ascending=False).index).head(top_n)
    df = df[df['metric'] == metric]
    df = df[df['qc_metric'] == qc_metric]
    df.drop(columns=['metric'], inplace=True)

    table = Table(title=f"Spearman correlations (top {len(df)} rows)", box=box.MINIMAL)
    for c in cols:
      table.add_column(c, overflow="fold", justify="right" if c in ('correlation','p_value') else "left")

    def fmt(val, col):
      if pd.isna(val):
        return ""
      if col == 'correlation':
        return f"{val:.3f}"
      if col == 'p_value':
        return f"{val:.2e}"
      if col == 'significant':
        return "★" if bool(val) else ""
      return str(val)

    for _, row in df.iterrows():
      table.add_row(*[fmt(row[col], col) for col in cols])

    console.print(table)

Metric: mean, QC Metric: Image sharpness


                                Spearman correlations (top 30 rows)                                
                     ╷                 ╷             ╷          ╷             ╷          ╷         
  variable           │ qc_metric       │ correlation │  p_value │ significant │ category │ tissue  
╶────────────────────┼─────────────────┼─────────────┼──────────┼─────────────┼──────────┼────────╴
  summary_wm_median  │ Image sharpness │      -0.499 │ 2.17e-21 │ ★           │ median   │ wm      
  summary_bg_mean    │ Image sharpness │       0.491 │ 1.21e-20 │ ★           │ mean     │ bg      
  summary_bg_p95     │ Image sharpness │       0.488 │ 2.31e-20 │ ★           │ p95      │ bg      
  summary_wm_mean    │ Image sharpness │      -0.463 │ 2.78e-18 │ ★           │ mean     │ wm      
  summary_bg_stdv    │ Image sharpness │       0.400 │ 1.32e-13 │ ★           │ stdv     │ bg      
  summary_wm_p05     │ Image sharpness │      -0.387 │ 8.82e-13 │ ★           │ p05      │ wm      
  summary_wm_stdv    │ Image sharpness │       0.347 │ 2.04e-10 │ ★           │ stdv     │ wm      
  summary_wm_mad     │ Image sharpness │       0.342 │ 4.00e-10 │ ★           │ mad      │ wm      
  summary_csf_stdv   │ Image sharpness │      -0.302 │ 4.13e-08 │ ★           │ stdv     │ csf     
  summary_gm_p05     │ Image sharpness │      -0.264 │ 1.89e-06 │ ★           │ p05      │ gm      
  summary_gm_mad     │ Image sharpness │       0.255 │ 4.11e-06 │ ★           │ mad      │ gm      
  summary_gm_mean    │ Image sharpness │      -0.251 │ 6.13e-06 │ ★           │ mean     │ gm      
  summary_gm_median  │ Image sharpness │      -0.249 │ 6.95e-06 │ ★           │ median   │ gm      
  summary_gm_n       │ Image sharpness │      -0.229 │ 4.01e-05 │ ★           │ n        │ gm      
  summary_gm_stdv    │ Image sharpness │       0.223 │ 6.05e-05 │ ★           │ stdv     │ gm      
  summary_csf_mad    │ Image sharpness │      -0.204 │ 2.53e-04 │ ★           │ mad      │ csf     
  summary_wm_n       │ Image sharpness │      -0.192 │ 5.94e-04 │ ★           │ n        │ wm      
  summary_csf_p95    │ Image sharpness │      -0.188 │ 7.88e-04 │ ★           │ p95      │ csf     
  summary_csf_n      │ Image sharpness │      -0.172 │ 2.12e-03 │ ★           │ n        │ csf     
  summary_bg_k       │ Image sharpness │      -0.171 │ 2.22e-03 │ ★           │ k        │ bg      
  summary_wm_k       │ Image sharpness │       0.152 │ 6.72e-03 │ ★           │ k        │ wm      
  summary_gm_k       │ Image sharpness │      -0.150 │ 7.67e-03 │ ★           │ k        │ gm      
  summary_gm_p95     │ Image sharpness │      -0.138 │ 1.41e-02 │ ★           │ p95      │ gm      
  summary_csf_p05    │ Image sharpness │       0.123 │ 2.88e-02 │ ★           │ p05      │ csf     
  summary_wm_p95     │ Image sharpness │      -0.107 │ 5.72e-02 │             │ p95      │ wm      
  summary_bg_median  │ Image sharpness │       0.094 │ 9.53e-02 │             │ median   │ bg      
  summary_bg_mad     │ Image sharpness │       0.094 │ 9.53e-02 │             │ mad      │ bg      
  summary_bg_n       │ Image sharpness │      -0.079 │ 1.61e-01 │             │ n        │ bg      
  summary_csf_mean   │ Image sharpness │      -0.073 │ 1.94e-01 │             │ mean     │ csf     
  summary_csf_median │ Image sharpness │      -0.057 │ 3.14e-01 │             │ median   │ csf     
                     ╵                 ╵             ╵          ╵             ╵          ╵

Metric: mean, QC Metric: Ringing


                             Spearman correlations (top 24 rows)                             
                     ╷           ╷             ╷          ╷             ╷          ╷         
  variable           │ qc_metric │ correlation │  p_value │ significant │ category │ tissue  
╶────────────────────┼───────────┼─────────────┼──────────┼─────────────┼──────────┼────────╴
  summary_wm_median  │ Ringing   │      -0.419 │ 7.04e-15 │ ★           │ median   │ wm      
  summary_wm_mean    │ Ringing   │      -0.376 │ 4.34e-12 │ ★           │ mean     │ wm      
  summary_bg_stdv    │ Ringing   │       0.335 │ 9.63e-10 │ ★           │ stdv     │ bg      
  summary_wm_p05     │ Ringing   │      -0.322 │ 4.22e-09 │ ★           │ p05      │ wm      
  summary_wm_stdv    │ Ringing   │       0.296 │ 7.93e-08 │ ★           │ stdv     │ wm      
  summary_bg_mean    │ Ringing   │       0.261 │ 2.50e-06 │ ★           │ mean     │ bg      
  summary_wm_mad     │ Ringing   │       0.255 │ 4.25e-06 │ ★           │ mad      │ wm      
  summary_wm_k       │ Ringing   │       0.244 │ 1.16e-05 │ ★           │ k        │ wm      
  summary_bg_p95     │ Ringing   │       0.229 │ 3.90e-05 │ ★           │ p95      │ bg      
  summary_csf_stdv   │ Ringing   │      -0.228 │ 4.24e-05 │ ★           │ stdv     │ csf     
  summary_csf_p05    │ Ringing   │       0.223 │ 6.06e-05 │ ★           │ p05      │ csf     
  summary_gm_mad     │ Ringing   │       0.222 │ 6.90e-05 │ ★           │ mad      │ gm      
  summary_gm_p05     │ Ringing   │      -0.207 │ 2.13e-04 │ ★           │ p05      │ gm      
  summary_gm_stdv    │ Ringing   │       0.193 │ 5.39e-04 │ ★           │ stdv     │ gm      
  summary_gm_median  │ Ringing   │      -0.190 │ 6.94e-04 │ ★           │ median   │ gm      
  summary_gm_mean    │ Ringing   │      -0.187 │ 8.40e-04 │ ★           │ mean     │ gm      
  summary_gm_p95     │ Ringing   │      -0.107 │ 5.63e-02 │             │ p95      │ gm      
  summary_gm_k       │ Ringing   │      -0.091 │ 1.08e-01 │             │ k        │ gm      
  summary_csf_n      │ Ringing   │       0.081 │ 1.51e-01 │             │ n        │ csf     
  summary_csf_p95    │ Ringing   │      -0.076 │ 1.74e-01 │             │ p95      │ csf     
  summary_wm_p95     │ Ringing   │      -0.075 │ 1.82e-01 │             │ p95      │ wm      
  summary_csf_k      │ Ringing   │       0.070 │ 2.15e-01 │             │ k        │ csf     
  summary_csf_median │ Ringing   │       0.064 │ 2.55e-01 │             │ median   │ csf     
  summary_csf_mad    │ Ringing   │      -0.051 │ 3.62e-01 │             │ mad      │ csf     
                     ╵           ╵             ╵          ╵             ╵          ╵

Metric: mean, QC Metric: CNR subcortical structures


...

                             Spearman correlations (top 27 rows)                             
                     ╷           ╷             ╷          ╷             ╷          ╷         
  variable           │ qc_metric │ correlation │  p_value │ significant │ category │ tissue  
╶────────────────────┼───────────┼─────────────┼──────────┼─────────────┼──────────┼────────╴
  summary_csf_mad    │ Ringing   │      -0.264 │ 1.94e-06 │ ★           │ mad      │ csf     
  summary_wm_mad     │ Ringing   │       0.227 │ 4.48e-05 │ ★           │ mad      │ wm      
  summary_wm_median  │ Ringing   │      -0.226 │ 4.81e-05 │ ★           │ median   │ wm      
  summary_csf_k      │ Ringing   │      -0.226 │ 4.92e-05 │ ★           │ k        │ csf     
  summary_wm_mean    │ Ringing   │      -0.223 │ 5.98e-05 │ ★           │ mean     │ wm      
  summary_bg_mad     │ Ringing   │      -0.201 │ 3.25e-04 │ ★           │ mad      │ bg      
  summary_csf_median │ Ringing   │       0.199 │ 3.52e-04 │ ★           │ median   │ csf     
  summary_gm_n       │ Ringing   │      -0.198 │ 3.83e-04 │ ★           │ n        │ gm      
  summary_bg_p05     │ Ringing   │      -0.192 │ 5.75e-04 │ ★           │ p05      │ bg      
  summary_bg_median  │ Ringing   │      -0.192 │ 5.75e-04 │ ★           │ median   │ bg      
  summary_wm_p05     │ Ringing   │      -0.192 │ 6.00e-04 │ ★           │ p05      │ wm      
  summary_wm_k       │ Ringing   │       0.172 │ 2.07e-03 │ ★           │ k        │ wm      
  summary_csf_mean   │ Ringing   │       0.161 │ 4.00e-03 │ ★           │ mean     │ csf     
  summary_csf_p05    │ Ringing   │       0.135 │ 1.61e-02 │ ★           │ p05      │ csf     
  summary_wm_stdv    │ Ringing   │       0.131 │ 1.98e-02 │ ★           │ stdv     │ wm      
  summary_gm_p95     │ Ringing   │       0.129 │ 2.14e-02 │ ★           │ p95      │ gm      
  summary_bg_n       │ Ringing   │      -0.121 │ 3.09e-02 │ ★           │ n        │ bg      
  summary_csf_n      │ Ringing   │      -0.120 │ 3.32e-02 │ ★           │ n        │ csf     
  summary_gm_stdv    │ Ringing   │       0.110 │ 5.07e-02 │             │ stdv     │ gm      
  summary_gm_p05     │ Ringing   │      -0.090 │ 1.10e-01 │             │ p05      │ gm      
  summary_bg_stdv    │ Ringing   │       0.088 │ 1.17e-01 │             │ stdv     │ bg      
  summary_wm_p95     │ Ringing   │      -0.081 │ 1.49e-01 │             │ p95      │ wm      
  summary_gm_k       │ Ringing   │      -0.081 │ 1.52e-01 │             │ k        │ gm      
  summary_bg_mean    │ Ringing   │       0.079 │ 1.61e-01 │             │ mean     │ bg      
  summary_csf_p95    │ Ringing   │       0.077 │ 1.74e-01 │             │ p95      │ csf     
  summary_bg_k       │ Ringing   │       0.070 │ 2.12e-01 │             │ k        │ bg      
  summary_wm_n       │ Ringing   │      -0.058 │ 3.04e-01 │             │ n        │ wm      
                     ╵           ╵             ╵          ╵             ╵          ╵

Metric: sig_digits, QC Metric: CNR subcortical structures


                                     Spearman correlations (top 24 rows)                                     
                    ╷                            ╷             ╷          ╷             ╷          ╷         
  variable          │ qc_metric                  │ correlation │  p_value │ significant │ category │ tissue  
╶───────────────────┼────────────────────────────┼─────────────┼──────────┼─────────────┼──────────┼────────╴
  summary_csf_mad   │ CNR subcortical structures │      -0.342 │ 3.96e-10 │ ★           │ mad      │ csf     
  summary_wm_median │ CNR subcortical structures │      -0.328 │ 2.23e-09 │ ★           │ median   │ wm      
  summary_gm_n      │ CNR subcortical structures │      -0.321 │ 5.06e-09 │ ★           │ n        │ gm      
  summary_wm_mean   │ CNR subcortical structures │      -0.298 │ 6.11e-08 │ ★           │ mean     │ wm      
  summary_gm_mean   │ CNR subcortical structures │      -0.270 │ 1.02e-06 │ ★           │ mean     │ gm      
  summary_wm_p05    │ CNR subcortical structures │      -0.270 │ 1.11e-06 │ ★           │ p05      │ wm      
  summary_gm_p05    │ CNR subcortical structures │      -0.267 │ 1.43e-06 │ ★           │ p05      │ gm      
  summary_gm_median │ CNR subcortical structures │      -0.266 │ 1.57e-06 │ ★           │ median   │ gm      
  summary_csf_n     │ CNR subcortical structures │      -0.222 │ 6.90e-05 │ ★           │ n        │ csf     
  summary_csf_k     │ CNR subcortical structures │      -0.222 │ 6.93e-05 │ ★           │ k        │ csf     
  summary_bg_p95    │ CNR subcortical structures │      -0.208 │ 1.94e-04 │ ★           │ p95      │ bg      
  summary_bg_mad    │ CNR subcortical structures │      -0.206 │ 2.16e-04 │ ★           │ mad      │ bg      
  summary_wm_p95    │ CNR subcortical structures │      -0.203 │ 2.84e-04 │ ★           │ p95      │ wm      
  summary_bg_p05    │ CNR subcortical structures │      -0.198 │ 3.81e-04 │ ★           │ p05      │ bg      
  summary_bg_median │ CNR subcortical structures │      -0.198 │ 3.81e-04 │ ★           │ median   │ bg      
  summary_gm_stdv   │ CNR subcortical structures │       0.171 │ 2.29e-03 │ ★           │ stdv     │ gm      
  summary_csf_stdv  │ CNR subcortical structures │      -0.170 │ 2.39e-03 │ ★           │ stdv     │ csf     
  summary_gm_k      │ CNR subcortical structures │      -0.157 │ 4.98e-03 │ ★           │ k        │ gm      
  summary_csf_p95   │ CNR subcortical structures │      -0.154 │ 5.90e-03 │ ★           │ p95      │ csf     
  summary_wm_n      │ CNR subcortical structures │      -0.143 │ 1.08e-02 │ ★           │ n        │ wm      
  summary_wm_mad    │ CNR subcortical structures │       0.095 │ 9.01e-02 │             │ mad      │ wm      
  summary_csf_mean  │ CNR subcortical structures │      -0.094 │ 9.54e-02 │             │ mean     │ csf     
  summary_wm_stdv   │ CNR subcortical structures │       0.092 │ 1.03e-01 │             │ stdv     │ wm      
  summary_bg_k      │ CNR subcortical structures │       0.065 │ 2.50e-01 │             │ k        │ bg      
                    ╵                            ╵             ╵          ╵             ╵          ╵

Metric: sig_digits, QC Metric: CNR GM and WM


                               Spearman correlations (top 27 rows)                               
                     ╷               ╷             ╷          ╷             ╷          ╷         
  variable           │ qc_metric     │ correlation │  p_value │ significant │ category │ tissue  
╶────────────────────┼───────────────┼─────────────┼──────────┼─────────────┼──────────┼────────╴
  summary_wm_median  │ CNR GM and WM │      -0.328 │ 2.11e-09 │ ★           │ median   │ wm      
  summary_wm_mean    │ CNR GM and WM │      -0.306 │ 2.72e-08 │ ★           │ mean     │ wm      
  summary_wm_p05     │ CNR GM and WM │      -0.284 │ 2.69e-07 │ ★           │ p05      │ wm      
  summary_csf_mad    │ CNR GM and WM │      -0.273 │ 7.77e-07 │ ★           │ mad      │ csf     
  summary_bg_mad     │ CNR GM and WM │      -0.248 │ 7.59e-06 │ ★           │ mad      │ bg      
  summary_gm_n       │ CNR GM and WM │      -0.248 │ 7.84e-06 │ ★           │ n        │ gm      
  summary_bg_median  │ CNR GM and WM │      -0.240 │ 1.53e-05 │ ★           │ median   │ bg      
  summary_bg_p05     │ CNR GM and WM │      -0.240 │ 1.53e-05 │ ★           │ p05      │ bg      
  summary_csf_k      │ CNR GM and WM │      -0.215 │ 1.19e-04 │ ★           │ k        │ csf     
  summary_gm_p05     │ CNR GM and WM │      -0.198 │ 3.92e-04 │ ★           │ p05      │ gm      
  summary_gm_median  │ CNR GM and WM │      -0.186 │ 8.78e-04 │ ★           │ median   │ gm      
  summary_csf_n      │ CNR GM and WM │      -0.184 │ 9.77e-04 │ ★           │ n        │ csf     
  summary_bg_p95     │ CNR GM and WM │      -0.171 │ 2.28e-03 │ ★           │ p95      │ bg      
  summary_wm_mad     │ CNR GM and WM │       0.167 │ 2.87e-03 │ ★           │ mad      │ wm      
  summary_gm_k       │ CNR GM and WM │      -0.162 │ 3.75e-03 │ ★           │ k        │ gm      
  summary_gm_mean    │ CNR GM and WM │      -0.156 │ 5.29e-03 │ ★           │ mean     │ gm      
  summary_wm_p95     │ CNR GM and WM │      -0.130 │ 2.08e-02 │ ★           │ p95      │ wm      
  summary_gm_stdv    │ CNR GM and WM │       0.125 │ 2.57e-02 │ ★           │ stdv     │ gm      
  summary_wm_n       │ CNR GM and WM │      -0.125 │ 2.62e-02 │ ★           │ n        │ wm      
  summary_csf_median │ CNR GM and WM │       0.117 │ 3.80e-02 │ ★           │ median   │ csf     
  summary_gm_p95     │ CNR GM and WM │       0.114 │ 4.31e-02 │ ★           │ p95      │ gm      
  summary_csf_stdv   │ CNR GM and WM │      -0.082 │ 1.43e-01 │             │ stdv     │ csf     
  summary_csf_p05    │ CNR GM and WM │       0.076 │ 1.75e-01 │             │ p05      │ csf     
  summary_wm_stdv    │ CNR GM and WM │       0.075 │ 1.83e-01 │             │ stdv     │ wm      
  summary_bg_mean    │ CNR GM and WM │       0.071 │ 2.10e-01 │             │ mean     │ bg      
  summary_csf_p95    │ CNR GM and WM │      -0.052 │ 3.60e-01 │             │ p95      │ csf     
  summary_bg_n       │ CNR GM and WM │      -0.050 │ 3.75e-01 │             │ n        │ bg      
                     ╵               ╵             ╵          ╵             ╵          ╵

In [25]:
correlation = get_correlation(stats_summary_comp_annotated)
correlation_spearman = correlation[correlation.method == 'spearman'].copy()
correlation_spearman['significant'] = correlation_spearman['p_value'] < 0.05
for name, group in {'Higher is better': positive_correlation, 'Lower is better': negative_correlation, 'ICV': icvs}.items():
		correlation_spearman_group = correlation_spearman[correlation_spearman.variable.isin(group)]
		fig = px.scatter(
			correlation_spearman_group.sort_values(by=['metric', 'correlation'], ascending=False),
			x='correlation',
			y='variable',
			facet_row='metric',
			color='qc_metric',
			symbol='significant',
			title='Correlation between QC Metrics and Variables (Spearman) - ' + name,
			height=800,
   		width=800,
		)
		display(fig)


/tmp/ipykernel_4621/2570646539.py:22: FutureWarning:

The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.

/home/yohan/.local/lib/python3.10/site-packages/pandas/core/arraylike.py:399: RuntimeWarning:

divide by zero encountered in log

/tmp/ipykernel_4621/2570646539.py:16: ConstantInputWarning:

An input array is constant; the correlation coefficient is not defined.

/tmp/ipykernel_4621/2570646539.py:17: ConstantInputWarning:

An input array is constant; the correlation coefficient is not defined.



In [89]:
def qc_correlation_analysis(df_raw_qc, stat='sig', alpha=0.05):
    # --- CONFIG ---

    import numpy as np
    import pandas as pd
    import plotly.express as px
    import plotly.graph_objects as go
    import pingouin as pg
    import significantdigits as sd
    import plotly.io as pio
    from plotly.subplots import make_subplots
    
    import warnings
    warnings.filterwarnings("ignore", category=UserWarning)
    warnings.filterwarnings("ignore", category=RuntimeWarning)
    warnings.filterwarnings("ignore", message="DataFrameGroupBy.apply operated on the grouping columns")
    
    # ===== 1) Variability metrics =====
    df = df_raw_qc.copy()

    # Within-subject variability across repetitions (per subject, per variable)
    if stat == 'sig':
        agg_fun = (lambda x: sd.significant_digits(array=x, reference=x.mean(), basis=10))
    elif stat == 'std':
        agg_fun = np.std
    elif stat == 'mean':
        agg_fun = np.mean
    else:
        raise ValueError(f"Unknown stat: {stat}")

    within = (df.groupby(by=['subject','variable'],)['value']
                .apply(agg_fun)
                .reset_index(name='var_within'))

    # Between-site variability across subjects (per site, per variable)
    between = (df.groupby(by=['site','variable'])['value']
                    .apply(agg_fun)
                    .reset_index(name='var_between'))

    # ===== 2) QC aggregation =====
    # QC per subject (for within) — average if multiple rows per (subject, qc_metric)
    qc_subj = (df.groupby(by=['subject','qc_metric'])['qc_value']
                .mean().reset_index())

    # QC per site (for between)
    qc_site = (df.groupby(by=['site','qc_metric'])['qc_value']
                .mean().reset_index())

    # ===== 3) Spearman correlations (ρ, p) =====
    # WITHIN
    mw = within.merge(qc_subj, on='subject', how='inner')
    def _spearman(g):
        out = pg.corr(g['var_within'], g['qc_value'], method='spearman')[['r','p-val']].iloc[0]
        return pd.Series({'rho_within': out['r'], 'p_within': out['p-val']})

    corr_within = (mw.groupby(['variable','qc_metric'])
                    .apply(_spearman)
                    .reset_index())

    # BETWEEN
    mb = between.merge(qc_site, on='site', how='inner')
    def _spearman_b(g):
        out = pg.corr(g['var_between'], g['qc_value'], method='spearman')[['r','p-val']].iloc[0]
        return pd.Series({'rho_between': out['r'], 'p_between': out['p-val']})

    corr_between = (mb.groupby(['variable','qc_metric'])
                        .apply(_spearman_b)
                        .reset_index())

    # ===== 4) FDR (per heatmap) and combined table =====
    # FDR per qc_metric is often reasonable; here we FDR across all tests in the map
    _, p_within_fdr  = pg.multicomp(corr_within['p_within'].values,  method='fdr_bh')
    _, p_between_fdr = pg.multicomp(corr_between['p_between'].values, method='fdr_bh')
    corr_within['p_within_fdr']  = p_within_fdr
    corr_between['p_between_fdr'] = p_between_fdr

    corr = (corr_within
            .merge(corr_between, on=['variable','qc_metric'], how='outer'))

    # Δρ for comparison
    corr['rho_delta'] = corr['rho_within'] - corr['rho_between']
    # --- Fisher z transform of correlations ---
    corr["z_within_fisher"]  = np.arctanh(np.clip(corr["rho_within"],  -0.999999, 0.999999))
    corr["z_between_fisher"] = np.arctanh(np.clip(corr["rho_between"], -0.999999, 0.999999))

    # Δz in Fisher space
    corr["delta_fisher"] = corr["z_within_fisher"] - corr["z_between_fisher"]

    # Then standardize (z-score across all variable × qc_metric pairs)
    mu = corr["delta_fisher"].mean(skipna=True)
    sigma = corr["delta_fisher"].std(skipna=True)
    corr["z_delta"] = (corr["delta_fisher"] - mu) / sigma
    corr['p_z_delta'] = 2 * sp.stats.norm.sf(np.abs(corr['z_delta']))
    _, p_delta_fdr = pg.multicomp(corr['p_z_delta'].values, method='fdr_bh')
    corr['p_delta_fdr'] = p_delta_fdr


    # Order variables by strongest (most negative) within corr (robustness ↑)
    order_vars = (corr.groupby('variable')['rho_within']
                    .apply(lambda s: np.nanmin(s.values))
                    .sort_values(ascending=True).index.tolist())
    corr['variable'] = pd.Categorical(corr['variable'], categories=order_vars, ordered=True)

    # Keep a stable qc_metric order
    order_qc = sorted(corr['qc_metric'].dropna().unique().tolist())
    corr['qc_metric'] = pd.Categorical(corr['qc_metric'], categories=order_qc, ordered=True)

    # ===== 5) Heatmaps =====
    def add_star_annotations(
        fig,
        df,
        p_col,                         # name of the p-value column to threshold
        x_col="qc_metric",             # x axis column
        y_col="variable",              # y axis column
        thresholds=(0.05, 0.01, 0.001, 0.0001),  # from least to most stringent
        symbol="★",
        color="black",
        size=12
    ):
        """
        Adds significance stars to a Plotly fig for each (x,y) cell in df.
        Stars count = number of thresholds that p-value crosses (lower = more stars).
        e.g., p=0.0003 with (0.05,0.01,0.001,0.0001) -> 3 stars (p<0.001).
        """
        def p_to_stars(p):
            if p is None or not np.isfinite(p):
                return 0
            return sum(p < t for t in thresholds)

        anns = []
        for _, r in df.iterrows():
            p = r.get(p_col, None)
            nstars = p_to_stars(p)
            if nstars <= 0:
                continue
            anns.append(dict(
                x=str(r[x_col]),
                y=str(r[y_col]),
                text=symbol * nstars,
                showarrow=False,
                font=dict(size=size, color=color),
                xanchor="center",
                yanchor="middle"
            ))

        # Keep existing annotations, if any
        existing = list(fig.layout.annotations) if fig.layout.annotations else []
        fig.update_layout(annotations=existing + anns)

    # --- (a) ρ_within ---
    heat_w = corr.pivot(index='variable', columns='qc_metric', values='rho_within')
    fig_w = px.imshow(
        heat_w, color_continuous_scale='RdBu_r', zmin=-1, zmax=1, aspect='auto', height=800,
        title=f"Spearman ρ (QC vs within-subject variability) {stat}"
    )
    fig_w.update_xaxes(title='QC metric')
    fig_w.update_yaxes(title='Variable')
    # stars: FDR<alpha
    stars_w = corr.loc[corr["p_within_fdr"].notna()].copy()
    add_star_annotations(fig_w, stars_w, 'p_within_fdr', color='black')
    fig_w.update_layout(height=800, width=800)
    #fig_w.show()

    # --- (b) ρ_between ---
    heat_b = corr.pivot(index='variable', columns='qc_metric', values='rho_between')
    fig_b = px.imshow(
        heat_b, color_continuous_scale='RdBu_r', zmin=-1, zmax=1, aspect='auto', height=800,
        title=f"Spearman ρ (QC vs between-site variability) {stat}"
    )
    fig_b.update_xaxes(title='QC metric')
    fig_b.update_yaxes(title='Variable')
    stars_b = corr.loc[corr["p_between_fdr"].notna()].copy()
    add_star_annotations(fig_b, stars_b, 'p_between_fdr', color='white')
    fig_b.update_layout(height=800, width=800)
    #fig_b.show()

    # --- (c) Δρ = ρ_within − ρ_between ---
    # Negative Δρ (blue) → QC explains within-variability more than between-site variability (good for test-retest);
    # Positive Δρ (red) → QC explains between-site variability more (site/center effects).
    # Plot the z-scores
    heat_z = corr.pivot(index='variable', columns='qc_metric', values='z_delta')
    zmax = np.nanmax(np.abs(heat_z.values))

    fig_z = px.imshow(
        heat_z, color_continuous_scale='RdBu_r', zmin=-zmax, zmax=zmax, aspect='auto', height=800,
        title="Z-score (Fisher-corrected Δρ) – standardized QC explanation gap"
    )
    fig_z.update_xaxes(title='QC metric')
    fig_z.update_yaxes(title='Variable')
    stars_z = corr.loc[corr["p_delta_fdr"].notna()].copy()
    add_star_annotations(fig_z, stars_z, 'p_delta_fdr', color='white')
    fig_z.update_layout(height=800, width=800)
    # fig_z.show()
    
    # ===== 6) (Optional) compact summary table =====
    summary = corr[['variable','qc_metric','rho_within','p_delta_fdr','rho_between','p_between_fdr','rho_delta']].sort_values(
        ['variable','qc_metric']
    )
    summary.head()

    fig = make_subplots(
        rows=1, cols=2,
        subplot_titles=[fig_w.layout.title.text, fig_b.layout.title.text],
        shared_yaxes=True,
        horizontal_spacing=0.05
    )

    # Add traces
    fig.add_traces(fig_w.data, rows=1, cols=1)
    fig.add_traces(fig_b.data, rows=1, cols=2)

    # Merge annotations (stars)
    annotations = []
    if fig_w.layout.annotations:
        for ann in fig_w.layout.annotations:
            ann.update(dict(xref="x1", yref="y1"))
            annotations.append(ann)
    if fig_b.layout.annotations:
        for ann in fig_b.layout.annotations:
            ann.update(dict(xref="x2", yref="y2"))
            annotations.append(ann)

    # Merge annotations
    fig.update_layout(
        annotations=annotations,
        width=1600,
        height=800,
    )

    # --- FIX 1: propagate coloraxis (colormap) ---
    fig.layout.coloraxis = fig_w.layout.coloraxis

    # --- FIX 2: ensure all traces use it ---
    for t in fig.data:
        t.update(coloraxis="coloraxis")

    fig.show()



In [90]:
qc_correlation_analysis(df_raw_qc[df_raw_qc.variable.str.contains('summary')], stat='sig')

In [92]:
z = df_raw_qc[~df_raw_qc.variable.str.contains('summary')]
qc_correlation_analysis(z, stat='sig')

In [93]:
qc_correlation_analysis(df_raw_qc[df_raw_qc.variable.str.contains('summary')], stat='std')

In [94]:
qc_correlation_analysis(df_raw_qc[~df_raw_qc.variable.str.contains('summary')], stat='std')

In [95]:
qc_correlation_analysis(df_raw_qc[df_raw_qc.variable.str.contains('summary')], stat='mean')

In [96]:
qc_correlation_analysis(df_raw_qc[~df_raw_qc.variable.str.contains('summary')], stat='mean')

In [97]:
import pandas as pd, numpy as np
import statsmodels.api as sm
from scipy.stats import rankdata

# Rank-transform all variables
df_ = df_raw_qc[~df_raw_qc.variable.str.contains('summary')]
for qc_metric in ['Image sharpness', 'Ringing', 'CNR subcortical structures', 'CNR GM and WM']:
    df_metric = df_[df_['qc_metric'] == qc_metric]
    df_metric = df_metric.groupby(by=['variable', 'repetition']).agg({'value': ['mean', 'std'], 'qc_value': lambda x: x.unique()[0], 'qc_metric': lambda x : x.unique()[0]}).reset_index()
    df_metric.columns = ['variable', 'repetition', 'mean', 'std', 'qc', 'qc_metric']
    df_metric = df_metric[df_metric['qc_metric'] == qc_metric]
    df_metric = df_metric[['variable', 'mean', 'std', 'qc']].dropna()
    df_rank = df_metric[['qc', 'mean', 'std']].apply(rankdata)

    # Fit linear model on ranks
    X = sm.add_constant(df_rank[['mean', 'std']])
    y = df_rank['qc']
    model = sm.OLS(y, X).fit()
    display(model.summary())
    R2 = model.rsquared
    R = np.sqrt(R2)
    print(f"Multiple Spearman-like R = {R:.3f}, R² = {R2:.3f}")


<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                     qc   R-squared:                       0.000
Model:                            OLS   Adj. R-squared:                 -0.002
Method:                 Least Squares   F-statistic:                   0.04476
Date:                Wed, 19 Nov 2025   Prob (F-statistic):              0.956
Time:                        01:58:30   Log-Likelihood:                -7569.0
No. Observations:                1080   AIC:                         1.514e+04
Df Residuals:                    1077   BIC:                         1.516e+04
Df Model:                           2                                         
Covariance Type:            nonrobust                                         
==============================================================================
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
const        541.3637     16.472     32.866      0.000     509.043     573.684
mean           0.0237      0.084      0.280      0.780      -0.142       0.189
std           -0.0253      0.084     -0.299      0.765      -0.191       0.141
==============================================================================
Omnibus:                     4237.428   Durbin-Watson:                   2.168
Prob(Omnibus):                  0.000   Jarque-Bera (JB):              180.177
Skew:                          -0.269   Prob(JB):                     7.50e-40
Kurtosis:                       1.073   Cond. No.                     1.78e+03
==============================================================================

Notes:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
[2] The condition number is large, 1.78e+03. This might indicate that there are
strong multicollinearity or other numerical problems.
"""

Multiple Spearman-like R = 0.009, R² = 0.000


<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                     qc   R-squared:                       0.000
Model:                            OLS   Adj. R-squared:                 -0.002
Method:                 Least Squares   F-statistic:                   0.01218
Date:                Wed, 19 Nov 2025   Prob (F-statistic):              0.988
Time:                        01:58:31   Log-Likelihood:                -7578.7
No. Observations:                1080   AIC:                         1.516e+04
Df Residuals:                    1077   BIC:                         1.518e+04
Df Model:                           2                                         
Covariance Type:            nonrobust                                         
==============================================================================
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
const        540.7850     16.621     32.537      0.000     508.172     573.398
mean           0.0128      0.085      0.150      0.881      -0.154       0.180
std           -0.0133      0.085     -0.156      0.876      -0.181       0.154
==============================================================================
Omnibus:                     4035.419   Durbin-Watson:                   2.396
Prob(Omnibus):                  0.000   Jarque-Bera (JB):              179.984
Skew:                           0.000   Prob(JB):                     8.26e-40
Kurtosis:                       1.000   Cond. No.                     1.78e+03
==============================================================================

Notes:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
[2] The condition number is large, 1.78e+03. This might indicate that there are
strong multicollinearity or other numerical problems.
"""

Multiple Spearman-like R = 0.005, R² = 0.000


<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                     qc   R-squared:                       0.000
Model:                            OLS   Adj. R-squared:                 -0.002
Method:                 Least Squares   F-statistic:                  0.004856
Date:                Wed, 19 Nov 2025   Prob (F-statistic):              0.995
Time:                        01:58:31   Log-Likelihood:                -7646.3
No. Observations:                1080   AIC:                         1.530e+04
Df Residuals:                    1077   BIC:                         1.531e+04
Df Model:                           2                                         
Covariance Type:            nonrobust                                         
==============================================================================
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
const        540.9409     17.694     30.572      0.000     506.222     575.660
mean           0.0080      0.091      0.089      0.929      -0.170       0.186
std           -0.0089      0.091     -0.098      0.922      -0.187       0.169
==============================================================================
Omnibus:                     5676.414   Durbin-Watson:                   1.953
Prob(Omnibus):                  0.000   Jarque-Bera (JB):               82.375
Skew:                          -0.103   Prob(JB):                     1.30e-18
Kurtosis:                       1.663   Cond. No.                     1.78e+03
==============================================================================

Notes:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
[2] The condition number is large, 1.78e+03. This might indicate that there are
strong multicollinearity or other numerical problems.
"""

Multiple Spearman-like R = 0.003, R² = 0.000


<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                     qc   R-squared:                       0.000
Model:                            OLS   Adj. R-squared:                 -0.002
Method:                 Least Squares   F-statistic:                   0.01899
Date:                Wed, 19 Nov 2025   Prob (F-statistic):              0.981
Time:                        01:58:31   Log-Likelihood:                -7538.9
No. Observations:                1080   AIC:                         1.508e+04
Df Residuals:                    1077   BIC:                         1.510e+04
Df Model:                           2                                         
Covariance Type:            nonrobust                                         
==============================================================================
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
const        540.4701     16.019     33.740      0.000     509.038     571.902
mean          -0.0158      0.082     -0.192      0.848      -0.177       0.145
std            0.0158      0.082      0.193      0.847      -0.145       0.177
==============================================================================
Omnibus:                     5270.721   Durbin-Watson:                   2.010
Prob(Omnibus):                  0.000   Jarque-Bera (JB):              184.196
Skew:                           0.553   Prob(JB):                     1.01e-40
Kurtosis:                       1.306   Cond. No.                     1.78e+03
==============================================================================

Notes:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
[2] The condition number is large, 1.78e+03. This might indicate that there are
strong multicollinearity or other numerical problems.
"""

Multiple Spearman-like R = 0.006, R² = 0.000


In [98]:
import pingouin as pg
df_results = pd.DataFrame()
df_raw = df_raw[df_raw['variable'] != 'provenance']

for variable in df_raw['variable'].unique():
    print(f"ANOVA for variable: {variable}")
    df_var = df_raw[df_raw['variable'] == variable].copy()

    # Ensure categorical factors (pingouin/statsmodels expects categorical within/between factors)
    df_var['repetition'] = df_var['repetition'].astype('category')
    df_var['site'] = df_var['site'].astype('category')

    # Basic checks to avoid errors from degenerate cases
    if df_var['repetition'].nunique() < 2:
        print("  Skipping: less than 2 repetition levels")
        continue
    if df_var['site'].nunique() < 2:
        print("  Skipping: less than 2 site levels")
        continue
    if df_var['subject'].nunique() < 2:
        print("  Skipping: less than 2 subjects")
        continue

    try:
        anova_results = pg.mixed_anova(data=df_var, dv='value', within='repetition', between='site', subject='subject')
        anova_results['variable'] = variable
    except KeyError as e:
        # Workaround: some pingouin/statsmodels combos raise KeyError: 'eps'.
        # Try a safer fallback: run a two-way between ANOVA on aggregated values (if meaningful),
        # or skip when the mixed model infrastructure fails.
        print(f"  mixed_anova failed with KeyError: {e}.")
        continue
    except Exception as e:
        print(f"  mixed_anova failed with unexpected error: {e}. Skipping this variable.")
        continue

    df_results = pd.concat([df_results, anova_results], axis=0, ignore_index=True)

df_results

ANOVA for variable: cjv
ANOVA for variable: cnr
ANOVA for variable: efc
ANOVA for variable: fber
ANOVA for variable: fwhm_avg
ANOVA for variable: fwhm_x
ANOVA for variable: fwhm_y
ANOVA for variable: fwhm_z
ANOVA for variable: icvs_csf
ANOVA for variable: icvs_gm
ANOVA for variable: icvs_wm
ANOVA for variable: inu_med
ANOVA for variable: inu_range
ANOVA for variable: qi_1
  mixed_anova failed with KeyError: 'eps'.
ANOVA for variable: qi_2
ANOVA for variable: rpve_csf
ANOVA for variable: rpve_gm
ANOVA for variable: rpve_wm
ANOVA for variable: size_x
ANOVA for variable: size_y
  mixed_anova failed with KeyError: 'eps'.
ANOVA for variable: size_z
ANOVA for variable: snr_csf
ANOVA for variable: snr_gm
ANOVA for variable: snr_total
ANOVA for variable: snr_wm
ANOVA for variable: snrd_csf
ANOVA for variable: snrd_gm
ANOVA for variable: snrd_total
ANOVA for variable: snrd_wm
ANOVA for variable: spacing_x
ANOVA for variable: spacing_y
ANOVA for variable: spacing_z
ANOVA for variable: summary_bg

Source          SS  DF1   DF2            MS          F  \
0           site   17.069892    5    40  3.413978e+00   8.030795   
1     repetition    0.000300   29  1160  1.035868e-05   0.773021   
2    Interaction    0.002288  145  1160  1.577626e-05   1.177310   
3           site  125.207394    5    40  2.504148e+01  11.272036   
4     repetition    0.002875   29  1160  9.915473e-05   0.977631   
..           ...         ...  ...   ...           ...        ...   
184   repetition    0.000044   29  1160  1.512449e-06   1.113473   
185  Interaction    0.000133  145  1160  9.159461e-07   0.674325   
186         site   20.505350    5    40  4.101070e+00  21.749050   
187   repetition    0.000173   29  1160  5.966343e-06   1.136037   
188  Interaction    0.002449  145  1160  1.689130e-05   3.216233   

            p-unc       np2       eps        variable  p-GG-corr sphericity  \
0    2.571712e-05  0.500960       NaN             cjv        NaN        NaN   
1    8.006045e-01  0.018959  0.234843             cjv        NaN        NaN   
2    8.536821e-02  0.128285       NaN             cjv        NaN        NaN   
3    7.998275e-07  0.584891       NaN             cnr        NaN        NaN   
4    5.000601e-01  0.023858  0.076376             cnr        NaN        NaN   
..            ...       ...       ...             ...        ...        ...   
184  3.103666e-01  0.027083  0.384987  tpm_overlap_wm        NaN        NaN   
185  9.985211e-01  0.077738       NaN  tpm_overlap_wm        NaN        NaN   
186  1.849145e-10  0.731084       NaN          wm2max        NaN        NaN   
187  2.833291e-01  0.027617  0.255140          wm2max        NaN        NaN   
188  6.953993e-28  0.286748       NaN          wm2max        NaN        NaN   

     W-spher  p-spher  
0        NaN      NaN  
1        NaN      NaN  
2        NaN      NaN  
3        NaN      NaN  
4        NaN      NaN  
..       ...      ...  
184      NaN      NaN  
185      NaN      NaN  
186      NaN      NaN  
187      NaN      NaN  
188      NaN      NaN  

[189 rows x 14 columns]

| Pattern                              | Interpretation                                                                                 |
| ------------------------------------ | ---------------------------------------------------------------------------------------------- |
| **site significant**, repetition not | Metric likely **scanner-dependent** but stable over time (site bias).                          |
| **repetition significant**, site not | Metric shows **test–retest sensitivity** or drift.                                             |
| **interaction significant**          | Metric behaves differently across sites over repetitions — possible site-specific instability. |
| **none significant**                 | Metric robust to site and time effects (ideal for harmonization).                              |


In [ ]:
id_vars = ['subject', 'variable', 'site', 'mean', 'std', 'var', 'min', 'max', 'sig_digits', 'qc', 'PATNO']
values = ['Image sharpness', 'Ringing', 'CNR subcortical structures', 'CNR GM and WM']
stats_qc_m = pd.melt(stats_qc, id_vars=id_vars, value_vars=values, var_name='QC_metric', value_name='QC_value')
stats_qc_m.sort_values(by=['QC_value'], ascending=True, inplace=True)
heigh=[2000, 3000, 1000]
for i,group in enumerate([positive_correlation, negative_correlation, icvs]):
    stats_qc_m_group = stats_qc_m[stats_qc_m.variable.isin(group)]
    stats_qc_m_group = stats_qc_m_group[stats_qc_m_group['sig_digits'] <= 7]
    fig = px.strip(stats_qc_m_group, x='QC_value', y='sig_digits', color='site', facet_col='QC_metric', facet_row='variable', title='Significant digits vs QC metrics', color_discrete_sequence=px.colors.diverging.Spectral, height=heigh[i]).update_xaxes(type='category').update_yaxes(matches=None)
    display(fig)
#px.strip(stats_qc_m[stats_qc_m.variable.str.contains('summary')], x='QC_value', y='sig_digits', color='site', facet_col='QC_metric', facet_row='variable', title='Significant digits vs QC metrics', height=4000).update_xaxes(type='category')

In [120]:
id_vars = ['subject', 'variable', 'site', 'mean', 'std', 'var', 'min', 'max', 'sig_digits', 'qc', 'PATNO']
values = ['Image sharpness', 'Ringing', 'CNR subcortical structures', 'CNR GM and WM']
stats_qc_m = pd.melt(stats_qc, id_vars=id_vars, value_vars=values, var_name='QC_metric', value_name='QC_value')
stats_qc_m.sort_values(by=['QC_value'], ascending=True, inplace=True)
height=[2000, 3000, 1000]
for i,group in enumerate([positive_correlation, negative_correlation, icvs]):
    stats_qc_m_group = stats_qc_m[stats_qc_m.variable.isin(group)]
    stats_qc_m_group = stats_qc_m_group[stats_qc_m_group['sig_digits'] < 7]
    fig = px.strip(stats_qc_m_group, x='QC_value', y='sig_digits', color='site', facet_col='QC_metric', facet_row='variable', title='Significant digits vs QC metrics', color_discrete_sequence=px.colors.diverging.Spectral, height=height[i]).update_xaxes(type='category').update_yaxes(matches=None)
    results = px.get_trendline_results(fig)
    display(fig)
#px.strip(stats_qc_m[stats_qc_m.variable.str.contains('summary')], x='QC_value', y='sig_digits', color='site', facet_col='QC_metric', facet_row='variable', title='Significant digits vs QC metrics', height=4000).update_xaxes(type='category')

## Covariance

## Mean vs Standard-deviation

In [129]:
from plotly.colors import make_colorscale, sample_colorscale
spectral_sampled = sample_colorscale(px.colors.diverging.Spectral, np.linspace(0,1,stats['site'].nunique()))
stats_summary = stats[stats.variable.str.contains('summary')]
stats_summary['category'] = stats_summary['variable'].apply(lambda x: x.split('_')[-1])
stats_summary['tissue'] = stats_summary['variable'].apply(lambda x: x.split('_')[1])
(px.scatter(stats_summary, x='mean', y='std', log_x=True, log_y=True, color='site', facet_row='tissue', facet_col='category', title='Significant digits vs Mean across subjects per metric', height=800, width=1600)
 .update_xaxes(exponentformat='power').update_yaxes(exponentformat='power')
    .add_scatter(x=np.logspace(-5,8,10), y=np.logspace(-5,8,10), mode='lines', line=dict(width=1, color='black', dash='dash'), name='0 sig', showlegend=False, row='all', col='all')
    .add_scatter(x=np.logspace(-5,8,10), y=np.logspace(-5,8,10)*10**-2, mode='lines', line=dict(width=1, color='DarkGray', dash='dash'), name='2 sig', showlegend=False, row='all', col='all')
    .add_scatter(x=np.logspace(-5,8,10), y=np.logspace(-5,8,10)*10**-4, mode='lines', line=dict(width=1, color='LightGray', dash='dash'), name='4 sig', showlegend=False, row='all', col='all')
    .add_scatter(x=np.logspace(-5,8,10), y=np.logspace(-5,8,10)*10**-6, mode='lines', line=dict(width=1, color='white', dash='dash'), name='6 sig', showlegend=False, row='all', col='all')
 )

/tmp/ipykernel_4621/2202098176.py:4: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/tmp/ipykernel_4621/2202098176.py:5: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [131]:
from matplotlib.pylab import f
from plotly.subplots import make_subplots
from itertools import product
import plotly.graph_objects as go
import tqdm

stats_others = stats[~stats.variable.str.contains('summary')]
stats_others = stats_others[~stats_others.variable.str.contains('size')]
stats_others = stats_others[~stats_others.variable.str.contains('spacing')]
showedlegend = {site: False for site in stats_others['site'].unique()}
print(f'Number of variables in others: {stats_others.variable.nunique()}')
nvars = stats_others.variable.nunique()
colormap = zip(plotly.colors.qualitative.T10 * 10, stats_others['site'].unique())
spectral_sampled = sample_colorscale(px.colors.diverging.Spectral, np.linspace(0,1,stats_others['site'].nunique()))
site_color_map = {site: color for color, site in colormap}
indexes = product(range(1,9), range(1,5))
variables = [
    'cjv', 'cnr', 'efc', 'fber',
    'fwhm_avg', 'fwhm_x', 'fwhm_y', 'fwhm_z',
    'snr_total', 'snr_csf', 'snr_gm', 'snr_wm',
    'snrd_total', 'snrd_csf', 'snrd_gm', 'snrd_wm',
    'icvs_csf', 'icvs_gm', 'icvs_wm', 'qi_1',
    'rpve_csf', 'rpve_gm', 'rpve_wm', 'qi_2',
    'tpm_overlap_csf', 'tpm_overlap_gm', 'inu_med', 'inu_range',
    'wm2max'
    ]

fig = make_subplots(rows=8, cols=4, subplot_titles=variables, vertical_spacing=0.03, horizontal_spacing=0.05, x_title='Mean', y_title='Std')
for (i, j), variable in tqdm.tqdm(zip(indexes, variables)):
    stats_var = stats_others[stats_others['variable'] == variable]
    for site in stats_var['site'].unique():
        fig.add_trace(go.Scatter(x=stats_var[stats_var['site'] == site]['mean'], 
                                 y=stats_var[stats_var['site'] == site]['std'], 
                                 mode='markers', 
                                 marker=dict(color=site_color_map[site]), 
                                 name=site,                                  
                                 showlegend=(not showedlegend[site])), 
                      row=i, col=j)
        showedlegend[site] = True
fig.update_layout(height=2000, width=1800, title_text="Significant digits vs Mean across subjects per metric - Others")
fig.update_xaxes(exponentformat='power', title='')
fig.update_xaxes(type='log')
fig.update_yaxes(type='log', exponentformat='power', title='')
fig.update_yaxes(matches='y5', row=2)
fig.update_yaxes(matches='y9', row=3)
fig.update_yaxes(matches='y13', row=4)
fig.update_yaxes(matches='y17', row=5)
fig.show()


Number of variables in others: 30


29it [00:00, 50.00it/s]
